# Final Practical Work: PageRank algorithm
## Authors: Alejandro Leonardo García Navarro, María Ángeles Magro Garrote
## NIAs: 100472710, 100472867

## What is PageRank?
The PageRank algorithm is a technique used by web search engines to rank web pages in their search results. It was named after Larry Page, one of the founders of Google, and is used to estimate the importance of website pages. In order to understand this algorithm in depth, there are some definitions that must be graped:

### Definitions
1. PageRank: This is a numeric value that represents how important a page is on the web. It is based on the idea that important pages are likely to receive more links from other websites.
2. Link Analysis: This algorithms considers the number and quality of links to a page to dermine a rough estimate of the website's importance. 
3. Damping Factor: This is a value between 0 and 1 that represents the probability that a person will continue clicking on links. If, for example, the value is 0.85, there is an 85% chance that a user will click on a link, and a 15% chance they will stop browing.

### How it works?
Generally, this algorithm works as follows:
1. Initial Assignment: Each page is given an initial rank. 
2. Link Evaluation: The algorithm evaluates all outbound links from a page. The PageRank value is equally distributed across these links.
3. Rank Calculation: The PageRank value for each page is calculated based on the PageRanks of pages linking to it. 

### Example
We consider it might be better to provide some example to have a better understanding of the algorithm.

Imagine a simple network of four web pages (A, B, C, D) where:
- Page A links to B, C, and D.
- Page B links to D.
- Page C links to B.
- Page D has no outbound links.

In the initial stage, all pages (A, B, C, D) might be assigned a PageRank of 1. Page D, despite having no outbound links, will receive PageRank from A, B, and C, possibly making it the highest-ranked page. Pages B and C will receive less PageRank since they have fewer inbound links. Through several iterations of the algorithm, the PageRank values will adjust and this will be repeated until convergence. 

### Modern Context
Even though PageRank was crucial in the early development of Google's search engine, nowadays is just one of many factors in their current ranking algorithms. PageRank laid the groundwork for understanidng web page importance based on link structures, but it is now part of a much more complex system in determining page rankings in search results.

## Import necessary libraries

In [ ]:
# Import all the classes and types available in the pyspark.sql.types module. It provides classes for different types of data. These classes are used to define the schema of DataFrames in Spark.
from pyspark.sql.types import *

# Imports all the functions available in the pyspark.sql.functions module. This is another module in PySpark, which provides a wide range of functions for data manipulation and transformation.
from pyspark.sql.functions import * 

## Implementing PageRank
1. Exploration of the dataset.
2. Identification of links.
3. Create the Forward Links table.
4. Create the Backward Links table.
5. PageRank algorithm.

### 1. Exploration of the dataset

An initial exploration of the provided Wikipedia dataset can offer valuable insights into its structure and content. 

In [ ]:
# First off, let's load the complete dataset. The line of code from below is a function call in Apache Spark, and works as follows:
# 1. spark.read.parquet: 
#   - spark: This represents the Spark session, an entry point to programming Spark with the Dataset and DataFrame API.
#   - read: This is a method of the Spark session that is used to load data into a DataFrame.
#   - parquet: This is a specific method of the "read" API. It is used to load Parquet files. Parquet is a columnar storage file format that is optimized for use with big data processing tools.

# 2. dbfs:/databricks-datasets/wikipedia-datasets/data-001/en_wikipedia/articles-only-parquet: This is the file path where the Parquet files are stored.

# 3. wikipediaDF: Finally, we assign the resulting DataFrame to a variable named "wikipediaDF".

wikipediaDF = spark.read.parquet("dbfs:/databricks-datasets/wikipedia-datasets/data-001/en_wikipedia/articles-only-parquet")

In [ ]:
# Count the number of rows of the complete dataset
wikipediaDF.count()

Out[3]: 5823210

In [ ]:
# Reducing the dataset to the 0.01% randomly (as stated)
sampleDF = wikipediaDF.sample(fraction=0.0001, seed=1234)

In [ ]:
# Count the number of rows of the sampleDF
sampleDF.count()

Out[5]: 610

In [ ]:
# Show the first 5 rows
sampleDF.show(5)  

+--------------------+------+----------+-------------------+----------------+------------------+--------------------+
|               title|    id|revisionId|  revisionTimestamp|revisionUsername|revisionUsernameId|                text|
+--------------------+------+----------+-------------------+----------------+------------------+--------------------+
|      Andrea Alciato|  1960| 681313521|2015-09-16 13:55:24|         AvicBot|          11952314|[[Image:Andrea Al...|
|      Geri and Freki| 12457| 680263770|2015-09-09 19:13:11|       Bloodofox|            308199|[[File:Odin, der ...|
|             470s BC| 47735| 561793018|2013-06-27 08:21:04|    Magioladitis|           1862829|{{Unreferenced|da...|
|                SIDS| 71632| 670295127|2015-07-07 02:34:42|    Grandpallama|           5406562|'''SIDS''' may re...|
|The Passion of th...|195246| 682394539|2015-09-23 13:04:38|         Doniago|           7021758|{{About|the film|...|
+--------------------+------+----------+----------------

The dataset includes columns "title," "id," "revisionId," "revisionTimestamp," "revisionUsername," "revisionUsernameId," and "text." The "title" column likely represents the title of the Wikipedia page, while "id" and "revisionId" are identifiers. The "revisionTimestamp" and "revisionUsername" provide information about the latest revision, and "text" contains the content of the Wikipedia article. The important information which will be used is stored in the columns named “title”, “id” and “text”.

### 2. Identification of links

To analyze the connectivity between Wikipedia pages and effectively implement the PageRank algorithm, we need to extract outgoing links from the textual content of each article. A <b> User-Defined Function (UDF) </b> will be crucial to achieve this, as it allows us to apply a customized analysis to the "text" field of our dataset. This analysis task involves identifying and extracting links enclosed within double brackets. This UDF will be a crucial step in the preparation for constructing the subsequent direct links matrix, essential for the implementation of the PageRank algorithm.

The "text" column holds the raw content of Wikipedia articles (shown below), including descriptions, citations, and links enclosed in double brackets ([[link]]). Extracting these links is crucial for analyzing the necessary relationships between articles, forming the basis for the PageRank.

In [ ]:
# Example of a text instance
text_for_first_row = sampleDF.select("text").head(1)[0][0]
print(text_for_first_row)

[[Image:Andrea Alciato 1584.JPG|right|thumb|Portrait of Andrea Alciato, reproduced from the 1584 edition of his emblem book]][[File:Andreas-Alciatus-Opera-omnia MG 0360.tif|thumb|Engraving of Andrea Alciato]]  '''Andrea Alciato''' (8 May 1492 – 12 January 1550),<ref>{{cite book|last=Bregman|first=Alvan|title=Emblemata: The emblem books of Andrea Alciato|year=2007|publisher=Bird & Bull Press|location=Newtown, Pa}}</ref> commonly known as '''Alciati''' ('''Andreas Alciatus'''), was an Italian [[jurist]] and writer.<ref>D. Bianchi, 1913. "L'opera letteraria e storica di Andrea Alciato", Archivio storico lombardo'', 4th series'''20''':47-57.</ref>  He is regarded as the founder of the French school of [[legal humanists]].  ==Biography== Alciati was born in [[Alzate Brianza]], near [[Milan]], and settled in France in the early 16th century. He displayed great literary skill in his exposition of the laws, and was one of the first to interpret the [[civil law (common law)|civil law]] by the h

The parse_text function is designed to extract meaningful links from the text column of Wikipedia articles for the PageRank algorithm. The general idea is to extract all content within double brackets ([[ ]]), representing potential links (not external references and resources which are not defined between double brackets).

Despite that, there are several considerations that must be taken into account: 
1) Images and file links have more information apart from the "name" of the image such as "right", "thumb" or captions. This information has to do with the view of the image and should be excluded. Notice this examples from the previous text:
    * [[Image:Andrea Alciato 1584.JPG|right|thumb|Portrait of Andrea Alciato, reproduced from the 1584 edition of his emblem book]]
    * [[File:Andreas-Alciatus-Opera-omnia MG 0360.tif|thumb|Engraving of Andrea Alciato]]
    We should only keep the text after "File:" or "Image:" until "|".

2) Category's links must be fixed when it comes to their format. For example:
    * [[Category:Italian Renaissance humanists]] 
    We should keep all the text after "Category:".

3) There can be several links inside a double bracket. For example:
    * [[civil law (common law)|civil law]]
    In this case, there are two links inside the double brackets and should be divided by the "|".


This ensures, first, that the PageRank algorithm can focus on meaningful relationships betweek Wikipedia pages. By filtering out these less informative links, the algorithm can better identify and prioritize the influence of pages that are more content-rich and interconnected, leading to a more accurate representation of page importance in the network. Then, ensuring a correct format will provide consistency, less noise and better performance of the algorithm.


In [ ]:
def parse_text(text):
    text = text.lower()
    links = []
    
    # Starting "[["
    start_index = text.find('[[')

    # Continue searching for links until there are no more
    while start_index != -1:
        # Find the ending index of the current link
        end_index = text.find(']]', start_index)

        # Extract the link substring
        block = text[start_index + 2:end_index]
    
        # For format file or image
        if "file:" in block or "image:" in block:
            block_initial_index = block.find(":")
            block_final_index = block.find("|")
            # Extract the link from the block and append it to the links list
            links.append(block[block_initial_index + 1:block_final_index])
        
        # For format [[ link1|link2 ]]
        elif "|" in block:
            # Split the block using '|' as a delimiter and append each element to the list
            for part in block.split("|"):
                links.append(part)

        # For format file or image
        elif "category:" in block:
            block_initial_index = block.find(":")
            # Extract the link from the block and append it to the links list
            links.append(block[block_initial_index+1:len(block)])

        # For format [[link]]
        else:
            # Append the entire block as a link to the links list
            links.append(block)

        # Find the starting index of the next link
        start_index = text.find('[[', end_index + 1)

    # Remove any empty strings from the final links list
    return links

We can check the functionality of parse_text calling it with the previous showed blocked of text. 

In [ ]:
parse_text(text_for_first_row)

Out[9]: ['andrea alciato 1584.jpg',
 'andreas-alciatus-opera-omnia mg 0360.tif',
 'jurist',
 'legal humanists',
 'alzate brianza',
 'milan',
 'civil law (common law)',
 'civil law',
 'tacitus',
 'emblemata',
 'emblem book',
 'europe',
 'great britain',
 'pavia',
 'emblema clxxxix.gif',
 '1492 births',
 '1550 deaths',
 '16th-century italian people',
 '16th-century latin-language writers',
 'italian historians',
 'italian jurists',
 'italian renaissance humanists',
 'people from the province of como',
 'roman law']

As observed above, the function worked, which means that it is now time to apply it to the sample dataset "sampleDF".

In [ ]:
# In order to apply it to the sample, we will carry out the following steps:
# 1. Use the function 'udf': It converts a regular Python function into a Spark UDF. Two parameters are indicated: 'parse_text' (Python function we are converting) and 'ArrayType(StringType())' (defines the return type of the UDF, which is an array of strings). This is necessary because Spark needs to know the data type of the function's output for its distributed computations.
parse_text_udf = udf(parse_text,ArrayType(StringType()))

# 2. Create a table with the titles, IDs, and links.
TempForwardDF = sampleDF.select(lower(col("title")).alias("title"), "id", parse_text_udf("text").alias("links"))

In [ ]:
# Finally, show the table
display(TempForwardDF)

title id links andrea alciato 1960 List(andrea alciato 1584.jpg, andreas-alciatus-opera-omnia mg 0360.tif, jurist, legal humanists, alzate brianza, milan, civil law (common law), civil law, tacitus, emblemata, emblem book, europe, great britain, pavia, emblema clxxxix.gif, 1492 births, 1550 deaths, 16th-century italian people, 16th-century latin-language writers, italian historians, italian jurists, italian renaissance humanists, people from the province of como, roman law) crossbar switch 45456 List(electronics, switch, rotary switch, crossover switch, telephony, circuit switching, sorting machine, semiconductor memory, fusible link, programmable read-only memory, sports bar, ethernet, rs-232, amx llc, amx, crestron, control4, multiswitch, microelectromechanical systems, mems, electromechanics, electromechanical, telephone switch, switching, telephone, western electric, stepping switch, televerket (sweden), televerket, gotthilf betulander, at&t corporation, 1xb, bell telephone labs, united states, ericsson, strowger switch, strowger, panel switch, panel, calling feature, plessey, txk, txe, reed relay, tandem switch, crossbar2.jpg, electrical connector, contacts, electromagnet, wire, txk, crossbar-hy1.jpg, bell system, crossbar-mini-hy2.jpg, c xbr sw hon jeh.jpg, tip and ring, balanced pair, four wire circuit, northern electric, sp1 switch, james cunningham, son and company, sp1 switch, 5xb switch, telephone, ringing (telephony), ring voltage, hertz, hz, common control, digital data, digital, strowger switch, strowger, stepping switch, crossbar-banjo2-hy.jpg, 1xb switch, switching fabric, common control, marker (telecommunications), marker, txk, russia, museum, science museum (london), science museum, london, strowger switch, multistage interconnection networks, uniform memory access, asynchronous transfer mode, wavefront arbiter, nonblocking minimal spanning switch, rf switch matrix, switches, telephone exchange equipment, electronic circuits) lafayette county, florida 72386 List(marquis de lafayette, county (united states), county, u.s. state, state, florida, 2010 united states census, 2010 census, county seat, mayo, florida, mayo, dry county, madison county, florida, madison county, dixie county, florida, dixie, marquis de lafayette, continental army, american revolutionary war, united states government publishing office, government printing office, suwannee river, dixie county, florida, dixie county, hal w. adams bridge, suspension bridge, old lafayette county courthouse, lafayette county courthouse (florida), lafayette county courthouse, u.s. census bureau, united states census bureau, suwannee county, florida, gilchrist county, florida, dixie county, florida, taylor county, florida, madison county, florida, census, united states census bureau, population density, race (united states census), white, race (united states census), black, race (united states census), african american, race (united states census), native american, race (united states census), asian, race (united states census), pacific islander, race (united states census), other races, race (united states census), hispanic, race (united states census), latino, marriage, married couples, per capita income, poverty line, republican party (united states), republican, democratic party (united states), democratic, third party (united states), other, u.s. presidential election, 2012, 2012, u.s. presidential election, 2008, 2008, u.s. presidential election, 2004, 2004, u.s. presidential election, 2000, 2000, lafayette blue springs state park, troy springs state park, gilchrist county, florida, gilchrist, dixie county, florida, dixie, taylor county, florida, taylor, mayo, florida, mayo, airline, florida, airline, alton, florida, alton, cooks hammock, florida, cooks hammock, day, florida, day, hatchbend, florida, hatchbend, midway, lafayette county, florida, midway, dry counties, columbia county, florida, columbia, dixie county, florida, dixie, hamilton county, florid

### 3. Create the Forward Links table

It might be a good idea to provide some background information regarding what is a "Forward Links" table. This is typicaly used to represent the structure of links or connections from one entity to another. In our case, a forward links table is used to map each Wikipedia page to all the entities it directly links to. For a Wikipedia page, these entitites would be other Wikipedia pages it references or links to.

The table structure tends to have:
1. ID Column: Contains unique identifiers for each page.
2. Links Columns: Contains a list of IDs to other pages that the current page links to; these are the "forward links".

This might be a little bit vague, but it can be clear with an example. Consider a Wikipedia page about "Artificial Intelligence" with ID "AI525". This page might have links to other pages like "Machine Learning", "Alan Turing", and "Neural Networks". The Forward Links table would then have an entry like: 
  - ID: AI525
  - Links: [ML456, AT789, NN101]

In [ ]:
# 1. Select the "title" and the "id" from the Wikipedia dataset:
titleidDF = wikipediaDF.select("id", lower(col("title")).alias("title"))

# 2. Convert the titles of the pages to ids using Spark DataFrame operations:
ForwardDF = TempForwardDF.select("id", explode("links").alias("link_title")) \
    .join(titleidDF.withColumnRenamed("id", "link_id"), col("link_title") == col("title"), "left_outer") \
    .groupBy("id") \
    .agg(collect_list("link_id").alias("links")) \
    .cache()

# 3. Optional: If you want to remove duplicates from the "links" array:
# ForwardDF = ForwardDF.withColumn("links", expr("DISTINCT links"))

# Now, ForwardDF contains the "id" and the corresponding array of linked pages "ids".

In [ ]:
# Finally, check the table
display(ForwardDF)

id links 10254961 List(42114862, 42114862, 42114862, 42114862, 1151871, 23753732, 23753732, 23753732, 23753732, 43175601, 43175601, 43175601, 43175601, 37050749, 37050749, 4689264, 4689264, 4689264, 4689264, 4689264, 7990680, 33077078, 33077078, 32960468, 32960468, 33160628, 33160628, 33160628, 33160628, 23472766, 23472766, 23472766, 23472766, 47374, 47374, 47374, 47374, 26938, 26938, 26938, 26938, 26938, 26938, 26938, 26938, 26938, 26938, 26938, 37005254, 37005254, 47902194, 6928256, 4552263, 7136620, 7136620, 7136620, 9633458, 9633458, 9633458, 9633458, 8630874, 33010453, 33010453, 30107030, 30107030, 30107030, 30107030, 12368109, 188079, 188079, 25538072, 25538072, 25538072, 38072627, 38072627, 38072627, 38072627, 20463779, 20463779, 21133596, 6144544, 6144544, 6144544, 6144544, 6144544, 6920765, 24207, 46945, 46847651, 46847651, 27352950, 40040170, 40040170, 9379306, 9379306, 9379306, 9379306, 9379306, 9379306, 241659, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 1423648, 7485883, 37128283, 37128283, 37128283, 37128283, 37128283, 37128283, 28267126, 32312414, 32312414, 32312414, 2035481, 15023724, 15023724, 15023724, 28266409, 28266409, 40941359, 40941359, 40941359, 40941359, 11196505, 43051322, 43051322, 2183474, 43846900, 43846900, 44766, 30126048, 30126048, 35983, 20232755, 20232755, 20232755, 20232755, 40609041, 40609041, 21607864, 21607864, 21607864, 21607864, 9860826, 8732124, 8732124, 8732124, 44295730, 44295730, 18739915, 18739915, 18739915, 18739915, 18739915, 18739915, 18739915, 8918704, 8918704, 8918704, 3360, 34561975, 34561975, 29627254, 29627254, 20351295, 20351295, 36790969, 36790969, 36790969, 36790969, 27906667, 18727355, 448519, 448519, 448519, 30681302, 30681302, 40869401, 40869401, 40869401, 40869401, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 295417, 34013907, 34013907, 21012279, 4548238, 30078628, 30078628, 10321484, 30931118, 30931118, 4985497, 4985497, 8713281, 33689, 13768583, 30335664, 30335664, 13905893, 13905893, 13905893, 13905893, 13905893, 13905893, 13905893, 13905893, 13905893, 363379, 363379, 363379, 363379, 363379, 363379, 7738452, 36225, 1199730, 37734364, 37734364, 35205659, 35205659, 38235303, 38235303, 34367118, 34367118, 34367118, 34367118, 35825, 35825, 39985647, 39985647, 39985647, 39985647, 14993168, 8314060, 13535824, 13535824, 13535824, 13535824, 28254920, 28254920, 29147247, 36039760, 36039760, 36039760, 36039760, 8732072, 10255354, 1370802, 1370802, 1370802, 1370802, 1370802, 1370802, 1370802, 1370802, 8310568, 2095560, 47068274, 47068274, 3766253, 3766253, 18740518, 18740518, 1418984, 1418984, 1418984, 1418984, 1418984, 1418984, 1418984, 7738742, 7738742, 33180, 11250, 11250, 11250, 11250, 3913129, 409341, 409341, 409341, 409341, 409341, 409341, 8533253, 177181, 25538831, 25538831, 25538831, 9806872, 4338052, 33268623, 33268623, 33268623, 33268623, 33268623, 33268623, 33268623, 33268623, 33268623, 33268623, 33268623, 33268623, 28664833, 2410340, 2410340, 2158641, 406072, 406072, 406072, 406072, 406072, 406072, 65711, 18621456, 18980510, 18980510, 7451852, 7451852, 7451852, 7451852, 7451852, 7451852, 435976, 435976, 435976, 435976, 435976, 435976, 3095179, 3545127, 3545127, 3545127, 213909, 213909, 27625424, 20678630, 20678630, 20678630, 20678630, 669345, 669345, 669345, 11867, 11867, 17574540, 30159142, 30159142, 30110535, 30110535, 1929307, 156618, 8806

### 4. Create the Backward Links table

This part of the project revolves around reversing the Forward Table that has been just created in order to store the information about "backward" links: the links from other webs to an specific web. This will be useful so that both, incoming and outgoing links, are taken into account when considering the rank of the web.

The dataFrame ForwardDF will be manipulated to reverse the links. The "links" array column is exploded, which means that each element of the array is expanded into a separate row, while retaining the original "id" column. The resulting DataFrame is then grouped by the exploded "link" column, and for each group, the corresponding "id" values are collected into a list using the collect_list aggregation function. The final DataFrame, named BackwardDF, consists of two columns: "link" and "reverse_links," where "link" represents the reversed links, and "reverse_links" contains a list of IDs associated with each unique reversed link.

In [ ]:
BackwardDF = ForwardDF.select("id", explode("links").alias("link")) \
                    .groupBy("link") \
                    .agg(collect_list("id").alias("reverse_links"))
                    
# Renaming columns to maintain 'id' and 'link'
BackwardDF = BackwardDF.withColumnRenamed("link", "id").withColumnRenamed("reverse_links", "links").cache()

In [ ]:
# Check the table
display(BackwardDF)

id links 20232755 List(10254961, 10254961, 10254961, 10254961) 90461 List(444466) 1557461 List(444466) 565939 List(15507375) 635367 List(28477011, 28477011, 28477011, 28477011) 143737 List(28477011) 13111485 List(1789800) 27207063 List(35697940) 26327739 List(37984558) 17627213 List(2992885) 156365 List(468770) 20497 List(468770, 468770) 237019 List(7984968) 17990997 List(15807279) 17285297 List(42881127, 42881127, 42881127, 42881127, 42881127) 9200161 List(36172406, 36172406, 36172406, 36172406, 36172406, 36172406, 36172406, 36172406, 36172406, 36172406) 47458229 List(36172406, 36172406, 36172406, 36172406, 36172406, 36172406, 36172406, 36172406) 12689594 List(2065420) 29730275 List(2610315, 2610315) 23015 List(39282074) 1853996 List(14177644) 12027 List(40641429, 37003621) 14625802 List(1603080) 184483 List(21391751) 191933 List(21391751) 37307 List(319602) 68090 List(26353259) 38153016 List(32806577, 32806577) 4543602 List(22746196) 6094276 List(5326948) 5962386 List(5326948) 21410449 List(22994171) 162105 List(32238027) 3815020 List(18515243) 39786415 List(41997657, 41997657) 39081188 List(41997657, 41997657) 44291152 List(45459197, 45459197) 1901970 List(39021837) 1951749 List(39021837) 37237101 List(37266671, 37266671, 37266671, 37266671) 434679 List(32145346) 6466 List(32734936) 46261169 List(12367925, 12367925) 78478 List(27996108) 550422 List(6322083) 90550 List(7983170, 7983170, 7983170, 7983170) 21958877 List(481722) 4266691 List(2081044, 2081044) 1154761 List(42184578) 12047861 List(5211159) 31050747 List(45689448) 190387 List(523694) 23057947 List(22086059) 328989 List(977436) 9840822 List(341746) 18902 List(3759880, 1533085) 62458 List(24538685) 9782491 List(2992885) 751669 List(468770) 35348624 List(468770, 468770) 5882667 List(12014575) 10349161 List(6839884) 32317240 List(39650398, 39650398) 1135310 List(7984968, 7984968) 3696476 List(7984968) 7018674 List(7984968) 1003088 List(39542531) 14148 List(16227422) 15967 List(2065420) 43434562 List(43725984, 43725984, 43725984, 43725984, 43725984, 43725984) 12124671 List(341860) 9207095 List(341860) 737 List(341860, 17642201) 1520837 List(31036263) 576409 List(30401678) 11157563 List(33538595, 33538595) 2912227 List(26352683, 40226581) 23886761 List(38396377) 22054164 List(39046344) 27455222 List(18681890) 412735 List(40226581) 290993 List(34525509) 10505102 List(16290296, 16290296) 8474767 List(1372640) 238725 List(21391751, 21391751, 21391751, 21391751, 21391751, 21391751) 1788051 List(26353259) 9239715 List(42813242) 1274036 List(4303206) 30952655 List(2027437, 2027437) 10439597 List(22994171, 22994171) 34510565 List(16050409, 16050409) 24355 List(16050409) 2169072 List(32303287, 32303287) 12578494 List(40018086, 40018086) 7097724 List(41997657) 30870683 List(44537850, 44537850) 8449472 List(21417246) 2724298 List(38254554, 38254554) 1707269 List(14109072) 17286793 List(44430966) 469850 List(16995303, 16995303) 21317166 List(35631742) 4190 List(35631742, 963533) 155190 List(23669181) 1944871 List(32873851, 32873851) 6956052 List(7983170) 18595 List(7983170, 7983170) 133814 List(35931247) 26787 List(2272396) 2272257 List(2272396) 2283346 List(27237073) 222740 List(37170566) 25759235 List(5211159) 146018 List(38970629) 40609041 List(10254961, 10254961) 3968643 List(11904019) 40652307 List(28477011, 28477011) 1119593 List(1499921) 457055 List(1116180, 6561068) 237715 List(35697940) 150793 List(468770, 468770) 155547 List(468770, 468770) 3674416 List(5765638, 5765638) 71821 List(2183137) 3352 List(8843153) 24632669 List(24610975) 2395117 List(312355) 30875813 List(166758, 166758) 931406 List(35727968) 3860497 List(341860, 341860) 4880701 List(42279824, 42279824) 1393698 List(2610315) 33148465 List(30401678, 30401678) 43620602 List(32794208, 32794208) 542488 List(38396377) 540627 List(18681890, 18681890) 439619 List(18681890) 18327016 List(18326980) 1143 List(8457335) 34882553 List(45050551, 45050551) 42244095 List(21391751, 21391751, 21391751, 21391751) 30860768 List(

### 5. PageRank algorithm

Now we are facing the last part of the project, where we must fully implement the **PageRank algorithm**. In order to keep it organized, we thought the best way of doing so would be to divide it into two parts: `First steps` and `Repeated application of the algorithm` (until convergence or max iterations are reached).

#### First steps
In this very first part, we will be setting up the initial environment or, in other words, the conditions for the PageRank algorithm to start iterating. This involves defining variables along the lines of: 
- `Damping Factor`: A constant used in the PageRank formula, representing the probability that a user continues to click on links. It is typically set to 0.85, as stated at the beginning of this project (please refer to this part for more information about the algorithm).
- `Max Iterations`: A threshold for the maximum number of iterations the algorithm should perform. It is a stopping criterion to prevent infinite looping in case the algorithm does not converge.
- `Threshold`: A small value that determines when to stop the iterations. If the change in PageRank values between iterations is less than this threshold, the algorithm is considered to have converged. 
- `PageRank Values`: Each page in the network is assigned an initial rank value, often set as the damping factor divided by the total number of pages.

In [ ]:
# Definition of variables:
damping_f = 0.85
max_iter = 20
threshold = 0.0000001
N = BackwardDF.count()

In [ ]:
# Now, we need to assign the PageRank values. In order to do this, we must explain the line of code from below:
# - BackwardDF.select("link"): First off, we use the 'select("link")' method to create a new DataFrame with just the 'link' column from BackwardDF. Each row in this column represents a unique page or link.
# - .withColumn("rank", lit(damping_f/N)): Here comes the important part. The method '.withColumn()' is used to add a new column to a DataFrame or replace an existing one. "rank" is the name of the new column being added, and 'lit(damping_f/N)' creates a Column type filled with a constant value. Here, damping_f is the damping factor, and N is the total number of pages. This expression calculates the initial PageRank value for each page, which is the damping factor divided by the total number of pages. The purpose of this line is to add a new column 'rank' to the DataFrame, where every row gets initialized with the same PageRank value. This initialization is a standard step in the PageRank algorithm where all pages start with an equal rank.
# - .toPandas(): Finally, this method converts the Spark DataFrame to a Pandas DataFrame. Pandas DataFrames are often easier to work with for further analysis. It's a matter of convenience and preference, as some operations might be simpler or more familiar in Pandas compared to Spark.
PageRankDF = (BackwardDF.select("id").withColumn("rank", lit(damping_f/N))).toPandas()

In [ ]:
# Check the pandas dataframe
display(PageRankDF)

id rank 20232755 7.460066701772863E-5 90461 7.460066701772863E-5 1557461 7.460066701772863E-5 565939 7.460066701772863E-5 635367 7.460066701772863E-5 143737 7.460066701772863E-5 13111485 7.460066701772863E-5 27207063 7.460066701772863E-5 26327739 7.460066701772863E-5 17627213 7.460066701772863E-5 156365 7.460066701772863E-5 20497 7.460066701772863E-5 237019 7.460066701772863E-5 17990997 7.460066701772863E-5 17285297 7.460066701772863E-5 9200161 7.460066701772863E-5 47458229 7.460066701772863E-5 12689594 7.460066701772863E-5 29730275 7.460066701772863E-5 23015 7.460066701772863E-5 1853996 7.460066701772863E-5 12027 7.460066701772863E-5 14625802 7.460066701772863E-5 184483 7.460066701772863E-5 191933 7.460066701772863E-5 37307 7.460066701772863E-5 68090 7.460066701772863E-5 38153016 7.460066701772863E-5 4543602 7.460066701772863E-5 6094276 7.460066701772863E-5 5962386 7.460066701772863E-5 21410449 7.460066701772863E-5 162105 7.460066701772863E-5 3815020 7.460066701772863E-5 39786415 7.460066701772863E-5 39081188 7.460066701772863E-5 44291152 7.460066701772863E-5 1901970 7.460066701772863E-5 1951749 7.460066701772863E-5 37237101 7.460066701772863E-5 434679 7.460066701772863E-5 6466 7.460066701772863E-5 46261169 7.460066701772863E-5 78478 7.460066701772863E-5 550422 7.460066701772863E-5 90550 7.460066701772863E-5 21958877 7.460066701772863E-5 4266691 7.460066701772863E-5 1154761 7.460066701772863E-5 12047861 7.460066701772863E-5 31050747 7.460066701772863E-5 190387 7.460066701772863E-5 23057947 7.460066701772863E-5 328989 7.460066701772863E-5 9840822 7.460066701772863E-5 18902 7.460066701772863E-5 62458 7.460066701772863E-5 9782491 7.460066701772863E-5 751669 7.460066701772863E-5 35348624 7.460066701772863E-5 5882667 7.460066701772863E-5 10349161 7.460066701772863E-5 32317240 7.460066701772863E-5 1135310 7.460066701772863E-5 3696476 7.460066701772863E-5 7018674 7.460066701772863E-5 1003088 7.460066701772863E-5 14148 7.460066701772863E-5 15967 7.460066701772863E-5 43434562 7.460066701772863E-5 12124671 7.460066701772863E-5 9207095 7.460066701772863E-5 737 7.460066701772863E-5 1520837 7.460066701772863E-5 576409 7.460066701772863E-5 11157563 7.460066701772863E-5 2912227 7.460066701772863E-5 23886761 7.460066701772863E-5 22054164 7.460066701772863E-5 27455222 7.460066701772863E-5 412735 7.460066701772863E-5 290993 7.460066701772863E-5 10505102 7.460066701772863E-5 8474767 7.460066701772863E-5 238725 7.460066701772863E-5 1788051 7.460066701772863E-5 9239715 7.460066701772863E-5 1274036 7.460066701772863E-5 30952655 7.460066701772863E-5 10439597 7.460066701772863E-5 34510565 7.460066701772863E-5 24355 7.460066701772863E-5 2169072 7.460066701772863E-5 12578494 7.460066701772863E-5 7097724 7.460066701772863E-5 30870683 7.460066701772863E-5 8449472 7.460066701772863E-5 2724298 7.460066701772863E-5 1707269 7.460066701772863E-5 17286793 7.460066701772863E-5 469850 7.460066701772863E-5 21317166 7.460066701772863E-5 4190 7.460066701772863E-5 155190 7.460066701772863E-5 1944871 7.460066701772863E-5 6956052 7.460066701772863E-5 18595 7.460066701772863E-5 133814 7.460066701772863E-5 26787 7.460066701772863E-5 2272257 7.460066701772863E-5 2283346 7.460066701772863E-5 222740 7.460066701772863E-5 25759235 7.460066701772863E-5 146018 7.460066701772863E-5 40609041 7.460066701772863E-5 3968643 7.460066701772863E-5 40652307 7.460066701772863E-5 1119593 7.460066701772863E-5 457055 7.460066701772863E-5 237715 7.460066701772863E-5 150793 7.460066701772863E-5 155547 7.460066701772863E-5 3674416 7.460066701772863E-5 71821 7.460066701772863E-5 3352 7.460066701772863E-5 24632669 7.460066701772863E-5 2395117 7.460066701772863E-5 30875813 7.460066701772863E-5 931406 7.460066701772863E-5 3860497 7.460066701772863E-5 4880701 7.460066701772863E-5 1393698 7.460066701772863E-5 33148465 7.460066701772863E-5 43620602 7.460066701772863E-5 542488 7.460066701772863E-5 540627 7.460066701772863E-5 439619 7.460066701772863E-5 18327016 7.460066701772863E-5 1143 7.46006670177

#### Repeated application of the algorithm
Once the first part of this section is done, we can now start applying the algorithm over and over. To accomplish this, we may give some indications on what we are trying to perform below:
1. Computing the Count of Links: First off, we may want to count the outbound links for each page to **make this information efficiently accessible** during the PageRank computation. We use `ForwardDF`, which contains infomration about the forward links of each page. Then, a DataFrame with two columns (id, count) is created and converted into a Pandas DataFrame. Finally, we considered broadcasting the count data, since it avoids the need to send this data over the network to each worker node multiple times.

2. Defining the PageRank Function: This constitutes the most important part of this last section. This function calculates the new PageRank for a given page. It has 3 parameters:
- `list_of_ids`: Contains the IDs of the pages that link to the current page.
- `current_id`: ID of the page for which the new PageRank is being calculated.
- `current_page_rank`: Pandas DataFrame containing the current PageRank of all pages.

3. Iterate until the maximum number of iterations is reached or convergence is achieved.
4. Display the new dataframe.

In [ ]:
# STEP 1:
linksDF = (ForwardDF.select("id", size("links").alias("count"))).toPandas()

In [ ]:
# STEP 2:
# Broadcasting linksDF to all worker nodes
linksDF_broadcast = sc.broadcast(linksDF) 

def page_ranking(list_of_ids, current_id, current_page_rank):
    # Retrieving the broadcasted linksDF
    links_values = linksDF_broadcast.value
    new_page_rank = 0
    
    # Iterating over the list of connected nodes
    for i in list_of_ids:
        # Checking if the node 'i' is present in the current_page_rank DataFrame
        if i in current_page_rank["id"].values: 
            old_page_rank = current_page_rank.loc[current_page_rank["id"] == i, "rank"].iat[0] 
        else:
            old_page_rank = 0
          
        # Checking if the node 'i' is present in the links_values DataFrame
        if i in links_values["id"].values:
            count = links_values.loc[links_values["id"] == i, "count"].iat[0] 
        else:
            count = 0
          
        # Updating the new_page_rank based on the old_page_rank and count
        new_page_rank += old_page_rank / count if count != 0 else 0

    # Applying the PageRank formula
    new_page_rank = (1 - damping_f) / N + damping_f * new_page_rank
    
    # Retrieving the current rank of the current_id
    current_rank = current_page_rank.loc[current_page_rank["id"] == current_id, "rank"].iat[0]
    
    # Calculating the difference between the new and current ranks
    difference  = new_page_rank - current_rank
    
    # Taking the absolute value of the difference
    if difference < 0:
        difference = -difference
    
    # Returning the new PageRank and the absolute difference
    return [float(new_page_rank), float(difference)]

In [ ]:
# STEP 3:
converged = False
iteration = 0

# Loop until the maximum number of iterations is reached or convergence is achieved
while iteration < max_iter and not converged:
  iteration += 1
  print("Iteration ", iteration) 

  # Defining a User Defined Function (UDF) using lambda function for calculating PageRank
  ranking_udf = udf(lambda links, ids: page_ranking(links, ids, PageRankDF), ArrayType(FloatType())) 
  
  # Applying the UDF to BackwardDF DataFrame to calculate the new PageRank and differences
  ranking = BackwardDF.select('id', ranking_udf('links', 'id').alias('rank'))                             
  
  # Converting the Spark DataFrame to Pandas DataFrame and selecting relevant columns
  PageRankDF = (ranking.select('id', ranking.rank[0].alias('rank'), ranking.rank[1].alias('difference'))).toPandas()
  
  # Checking convergence by comparing differences with the threshold
  converged = all(i < threshold for i in PageRankDF["difference"])

Iteration  1
Iteration  2
Iteration  3
Iteration  4
Iteration  5
Iteration  6


In [ ]:
# STEP 4:
PageRankDF = PageRankDF.filter(["id","rank"]).copy()
display(PageRankDF)        

id rank 20232755 1.3164824E-5 90461 1.3164824E-5 1557461 1.3164824E-5 565939 1.3164824E-5 635367 1.3164824E-5 143737 1.3164824E-5 13111485 1.3164824E-5 27207063 1.3164824E-5 26327739 1.3164824E-5 17627213 1.3164824E-5 156365 1.3164824E-5 20497 1.3164824E-5 237019 1.3164824E-5 17990997 1.3164824E-5 17285297 1.3164824E-5 9200161 1.3164824E-5 47458229 1.3164824E-5 12689594 1.3164824E-5 29730275 1.3164824E-5 23015 1.3164824E-5 1853996 1.3164824E-5 12027 1.3164824E-5 14625802 1.3164824E-5 184483 1.3164824E-5 191933 1.3164824E-5 37307 1.3164824E-5 68090 1.3164824E-5 38153016 1.3164824E-5 4543602 1.3164824E-5 6094276 1.3164824E-5 5962386 1.3164824E-5 21410449 1.3164824E-5 162105 1.3164824E-5 3815020 1.3164824E-5 39786415 1.3164824E-5 39081188 1.3164824E-5 44291152 1.3164824E-5 1901970 1.3164824E-5 1951749 1.3164824E-5 37237101 1.3164824E-5 434679 1.3164824E-5 6466 1.3164824E-5 46261169 1.3164824E-5 78478 1.3164824E-5 550422 1.3430306E-5 90550 1.3164824E-5 21958877 1.3164824E-5 4266691 1.3164824E-5 1154761 1.3164824E-5 12047861 1.3164824E-5 31050747 1.3164824E-5 190387 1.3164824E-5 23057947 1.3164824E-5 328989 1.3164824E-5 9840822 1.3164824E-5 18902 1.3164824E-5 62458 1.3164824E-5 9782491 1.3164824E-5 751669 1.3164824E-5 35348624 1.3164824E-5 5882667 1.3164824E-5 10349161 1.3164824E-5 32317240 1.3164824E-5 1135310 1.3164824E-5 3696476 1.3164824E-5 7018674 1.3164824E-5 1003088 1.3164824E-5 14148 1.3164824E-5 15967 1.3164824E-5 43434562 1.3164824E-5 12124671 1.3164824E-5 9207095 1.3164824E-5 737 1.3164824E-5 1520837 1.3164824E-5 576409 1.3164824E-5 11157563 1.3164824E-5 2912227 1.3164824E-5 23886761 1.3164824E-5 22054164 1.3164824E-5 27455222 1.3164824E-5 412735 1.3164824E-5 290993 1.3164824E-5 10505102 1.3164824E-5 8474767 1.3164824E-5 238725 1.3164824E-5 1788051 1.3164824E-5 9239715 1.3164824E-5 1274036 1.3164824E-5 30952655 1.3164824E-5 10439597 1.3164824E-5 34510565 1.3164824E-5 24355 1.3164824E-5 2169072 1.3164824E-5 12578494 1.3164824E-5 7097724 1.3164824E-5 30870683 1.3164824E-5 8449472 1.3164824E-5 2724298 1.3164824E-5 1707269 1.3164824E-5 17286793 1.3164824E-5 469850 1.3164824E-5 21317166 1.3164824E-5 4190 1.3164824E-5 155190 1.3164824E-5 1944871 1.3164824E-5 6956052 1.3164824E-5 18595 1.3164824E-5 133814 1.3164824E-5 26787 1.3164824E-5 2272257 1.3164824E-5 2283346 1.3164824E-5 222740 1.3164824E-5 25759235 1.3164824E-5 146018 1.3164824E-5 40609041 1.3164824E-5 3968643 1.3164824E-5 40652307 1.3164824E-5 1119593 1.3164824E-5 457055 1.3164824E-5 237715 1.3164824E-5 150793 1.3164824E-5 155547 1.3164824E-5 3674416 1.3164824E-5 71821 1.3164824E-5 3352 1.3164824E-5 24632669 1.3164824E-5 2395117 1.3164824E-5 30875813 1.3164824E-5 931406 1.3164824E-5 3860497 1.3164824E-5 4880701 1.3164824E-5 1393698 1.3164824E-5 33148465 1.3164824E-5 43620602 1.3164824E-5 542488 1.3164824E-5 540627 1.3164824E-5 439619 1.3164824E-5 18327016 1.3164824E-5 1143 1.3164824E-5 34882553 1.3164824E-5 42244095 1.3164824E-5 30860768 1.3164824E-5 1794354 1.3164824E-5 5974250 1.3164824E-5 163118 1.3164824E-5 4361554 1.3164824E-5 61344 1.3164824E-5 8596373 1.3164824E-5 43144204 1.3164824E-5 38195678 1.3164824E-5 5417026 1.3164824E-5 16263143 1.3164824E-5 1766038 1.3164824E-5 13185583 1.3164824E-5 202687 1.3164824E-5 25496496 1.3164824E-5 20665719 1.3164824E-5 6075795 1.3164824E-5 248867 1.3164824E-5 159433 1.3164824E-5 18260530 1.3164824E-5 2850414 1.3164824E-5 689617 1.3164824E-5 357190 1.3164824E-5 32715402 1.3164824E-5 37631976 1.3164824E-5 40097058 1.3164824E-5 24604653 1.3164824E-5 18024650 1.3164824E-5 685448 1.3164824E-5 9681718 1.3164824E-5 3128849 1.3164824E-5 8742961 1.3164824E-5 412343 1.3164824E-5 32960468 1.3164824E-5 3913129 1.3164824E-5 32129777 1.3164824E-5 9731047 1.3164824E-5 171975 1.3164824E-5 1745313 1.35487035E-5 27207030 1.3164824E-5 22688513 1.3164824E-5 172311 1.3164824E-5 33550 1.3164824E-5 54980 1.3164824E-5 18883554 1.3164824E-5 990794 1.3164824E-5 1136060 1.3164824E-5 451983 1.3164824E-5 6579025 1.3164824E-5 697901 1.3164824E-5 599674 1.3

## Conclusions (Alejandro Leonardo García Navarro)

After having obtained the results, it is high time we reach some conclusions. PageRank is a fundamental algorithm initially developed by Google's founders to rank webpages in search engine results. It operates on a simple but powerful principle: a webpage is considered important if it is linked to by other important webpages. The algorithm assigns a numeric value, known as the PageRank score, to each page on the web. This system creates a hierarchical structure of webpages, aiding search engines in identifying the most relevant and authoritative pages in response to a user's query. 

In completing this PageRank project, I have gained a deep understanding of the algorithm's mechanics and successfully implemented it in a big data context using PySpark. Our approach began with an in-depth exploration of how PageRank operates, focusing on link analysis, the significance of the damping factor, and the necessity for iterative calculations. This first knowledge was crucial for effectively applying the algorithm.

Addressing the project's technical aspects, we began with an initial exploration of the provided Wikipedia dataset, gaining insights into its structure and content. Recognizing the importance of the "title", "id", and "text" columns, we adapted our approach to focuse only on these key data elements. The implementation of a User-Defined Function (UDF) was a critical step, allowing us to extract outbound links from the textual content of Wikipedia articles. This UDF was designed to parse the text and extract meaningful links, while addressing various format considerations such as images, categories, and multiple links within a single bracket.

Then, we started with one of the most crucial phases of the project, the construction of the Forward and Backward Links tables. These were key in mapping the structure of links from and to each Wikipedia page, respectively. We carefully transformed the dataset to represent these link structures, understanding that they form the bases of the PageRank algorithm.

In this final phase, we implemented the PageRank algorithm itself. This involved setting up initial conditions, defining key variables, and then iteratively applying the PageRank formula. To be precise, we did the following: firstly, we counted the outbound links for each page to **make this information efficiently accessible** during the PageRank computation; secondly, we defined the PageRank function, which calculates the new PageRank for a given page; after that, the iterative process starts. As stated in the instructions, this had to be monitored to ensure that the algorithm converged to a stable state, using a threshold as a stopping criterion; finally, the dataframe is displayed.

Throughout this projet, we were keenly aware of the importance of **performance** and **scalability**, especially given the large scale of the Wikipedia dataset. Techniques like strategically using Pandas DataFrames only when required were employed to enhance performance and manage computational resources effectively. Here are some other examples:
1. Scalable Data Processing with Spark: The choice of Spark for data processing inherently addressed scalability. Spark's distributed nature allows for scaling out computations across multiple nodes, making it well-suited for handling increases in data volume. 
2. Modular Code Desing: We designed the code in sections, separating different stages of the PageRank calculation to make the code more manageable.
3. Pandas for Smaller Subsets of Data: As mentioned, in certain instances we used Pandas DataFrames for operations on smaller subsets of data. This approach leveraged the efficiency of Pandas for small-scale data manipulation, while relying on Spark for distributed processing of the larger dataset. This hybrid approach provided a balance between performance and ease of use.
4. Memory Management: Throughout the project, we were conscious of memory usage, especially given the large dataset. By optimizing data storage formats and using caching, we managed memory usage effectively, which is crucial for scalability.

In summary, this project involved a thorough exploration and implementation of the PageRank algorithm, focusing on the complexity of link analysis and iterative computation, and culminating in the successful application of these principles to a large, real-world dataset.